In [0]:
adlsAccountName = "fabaccelerla3wfpqdmcv7c"
sourceAdlsContainerName = "silver"
sinkAdlsContainerName = "silver"
sourceAdlsFolderName = "/cms/MedicareInpatientHospitalsByProviderAndService/"
#cms/MedicareInpatientHospitalsByProviderAndService/user0/medicareinpatienthospitals/
sinkAdlsFolderName = "/cms/MedicareInpatientHospitalsByProviderAndService/"
user = "abbott"
catalogdatabaseschema = "dev_silver.abbott"
databasetable = "medicareinpatienthospitals"
usertable = catalogdatabaseschema + "." + databasetable + user
print(usertable)
abfsspath = "abfss://" + sinkAdlsContainerName + "@" + adlsAccountName + ".dfs.core.windows.net" + sinkAdlsFolderName + user + "/gold/"
print(abfsspath)

dev_silver.abbott.medicareinpatienthospitalsabbott
abfss://silver@fabaccelerla3wfpqdmcv7c.dfs.core.windows.net/cms/MedicareInpatientHospitalsByProviderAndService/abbott/gold/


In [0]:
spark.conf.set(
    "fs.azure.account.key." + adlsAccountName + ".dfs.core.windows.net",
    dbutils.secrets.get(scope="autoloader-fabric",key="Adls2-KeySecret"))

In [0]:
dbutils.fs.ls("abfss://" + sourceAdlsContainerName + "@" + adlsAccountName + ".dfs.core.windows.net/")

[FileInfo(path='abfss://silver@fabaccelerla3wfpqdmcv7c.dfs.core.windows.net/CDC/', name='CDC/', size=0, modificationTime=1684896104000),
 FileInfo(path='abfss://silver@fabaccelerla3wfpqdmcv7c.dfs.core.windows.net/cms/', name='cms/', size=0, modificationTime=1686690029000)]

In [0]:
from  pyspark.sql.functions import *    
sqlstringdate = "select distinct twodigityear, year from " + usertable + " order by twodigityear"
dfdate = spark.sql(sqlstringdate)
display(dfdate)

twodigityear year 13 2013 14 2014 15 2015 16 2016 17 2017 18 2018 19 2019 20 2020 21 2021

In [0]:
from pyspark.sql.types import *
import json

jschemadate = '{"fields":[{"metadata":{},"name":"twodigityear","nullable":true,"type":"string"},{"metadata":{},"name":"year","nullable":true,"type":"string"}],"type":"struct"}'

schemadate = StructType.fromJson(json.loads(jschemadate))

In [0]:
dfdate.write.mode("overwrite").format("delta").option("mergeSchema", "true").option("schema", "schemadate").save("/mnt/sink/" + sinkAdlsFolderName + user + "/gold/date/")

In [0]:
from  pyspark.sql.functions import *    
sqlstringprov = "select distinct Rndrng_Prvdr_CCN, Rndrng_Prvdr_Org_Name, Rndrng_Prvdr_City, Rndrng_Prvdr_St, Rndrng_Prvdr_State_FIPS, Rndrng_Prvdr_Zip5, Rndrng_Prvdr_State_Abrvtn, Rndrng_Prvdr_RUCA, Rndrng_Prvdr_RUCA_Desc from " + usertable + " order by Rndrng_Prvdr_CCN"
dfprov = spark.sql(sqlstringprov)
display(dfprov)

Rndrng_Prvdr_CCN Rndrng_Prvdr_Org_Name Rndrng_Prvdr_City Rndrng_Prvdr_St Rndrng_Prvdr_State_FIPS Rndrng_Prvdr_Zip5 Rndrng_Prvdr_State_Abrvtn Rndrng_Prvdr_RUCA Rndrng_Prvdr_RUCA_Desc 10001 Southeast Alabama Medical Center Dothan 1108 Ross Clark Circle 01 36301 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10001 Southeast Health Medical Center Dothan 1108 Ross Clark Circle 01 36301 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10005 Marshall Medical Center South Boaz 2505 U S Highway 431 North 01 35957 AL 4 Micropolitan area core: primary flow within an urban cluster of 10,000 to 49,999 10005 Marshall Medical Centers South Campus Boaz 2505 U S Highway 431 North 01 35957 AL 4 Micropolitan area core: primary flow within an urban cluster of 10,000 to 49,999 10006 Eliza Coffee Memorial Hospital Florence 205 Marengo Street 01 35631 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10006 North Alabama Medical Center Florence 1701 Veterans Drive 01 35630 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10007 Mizell Memorial Hospital Opp 702 N Main St 01 36467 AL 7 Small town core: primary flow within an urban cluster of 2,500 to 9,999 10008 Crenshaw Community Hospital Luverne 101 Hospital Circle 01 36049 AL 3 Metropolitan area low commuting: primary flow 10% to <30% to a urbanized area of 50,000 and greater 10011 St Vincent's East Birmingham 50 Medical Park East Drive 01 35235 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10012 Dekalb Regional Medical Center Fort Payne 200 Med Center Drive 01 35968 AL 9 Small town low commuting: primary flow 10% to <30% to a urban cluster of 2,500 to 9,999 10012 Dekalb Regional Medical Center Fort Payne 200 Med Center Drive 01 35968 AL 10 Rural areas: primary flow to a tract outside a urbanized area of 50,000 and greater or UC 10012 Dekalb Regional Medical Center Fort Payne 200 Med Center Drive 01 35968 AL 7 Small town core: primary flow within an urban cluster of 2,500 to 9,999 10016 Shelby Baptist Medical Center Alabaster 1000 First Street North 01 35007 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10018 Callahan Eye Hospital Birmingham 1720 University Blvd 01 35233 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10018 Uab Callahan Eye Hospital Authority Birmingham 1720 University Blvd, Suite 500 01 35233 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10019 Helen Keller Memorial Hospital Sheffield 1300 South Montgomery Avenue 01 35660 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10021 Dale Medical Center Ozark 126 Hospital Ave 01 36360 AL 4.1 Secondary flow 30% to <50% to a urbanized area of 50,000 and greater 10022 Cherokee Medical Center Centre 400 Northwood Dr 01 35960 AL 3 Metropolitan area low commuting: primary flow 10% to <30% to a urbanized area of 50,000 and greater 10022 Floyd Cherokee Medical Center Centre 400 Northwood Dr 01 35960 AL 3 Metropolitan area low commuting: primary flow 10% to <30% to a urbanized area of 50,000 and greater 10023 Baptist Medical Center South Montgomery 2105 East South Boulevard 01 36116 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10024 Jackson Hospital & Clinic Inc Montgomery 1725 Pine Street 01 36106 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10025 George H. Lanier Memorial Hospital Valley 4800 48th St 01 36854 AL 4 Micropolitan area core: primary flow within an urban cluster of 10,000 to 49,999 10029 East Alabama Medical Center And Snf Opelika 2000 Pepperell Parkway 01 36801 AL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 10029 East Alabama Medical Center Ope

In [0]:
from  pyspark.sql.functions import *    
sqlstringdrg = "select distinct DRG_Cd, DRG_Desc from " + usertable + " order by DRG_Cd"
dfdrg = spark.sql(sqlstringdrg)
display(dfdrg)

DRG_Cd DRG_Desc 001 HEART TRANSPLANT OR IMPLANT OF HEART ASSIST SYSTEM WITH MCC 002 HEART TRANSPLANT OR IMPLANT OF HEART ASSIST SYSTEM WITHOUT MCC 003 ECMO OR TRACHEOSTOMY WITH MV >96 HOURS OR PRINCIPAL DIAGNOSIS EXCEPT FACE, MOUTH AND NEC 004 TRACHEOSTOMY WITH MV >96 HOURS OR PRINCIPAL DIAGNOSIS EXCEPT FACE, MOUTH AND NECK WITHOU 005 LIVER TRANSPLANT WITH MCC OR INTESTINAL TRANSPLANT 006 LIVER TRANSPLANT WITHOUT MCC 007 LUNG TRANSPLANT 008 SIMULTANEOUS PANCREAS AND KIDNEY TRANSPLANT 011 TRACHEOSTOMY FOR FACE, MOUTH AND NECK DIAGNOSES OR LARYNGECTOMY WITH MCC 012 TRACHEOSTOMY FOR FACE, MOUTH AND NECK DIAGNOSES OR LARYNGECTOMY WITH CC 013 TRACHEOSTOMY FOR FACE, MOUTH AND NECK DIAGNOSES OR LARYNGECTOMY WITHOUT CC/MCC 014 ALLOGENEIC BONE MARROW TRANSPLANT 016 AUTOLOGOUS BONE MARROW TRANSPLANT WITH CC/MCC 017 AUTOLOGOUS BONE MARROW TRANSPLANT WITHOUT CC/MCC 018 CHIMERIC ANTIGEN RECEPTOR (CAR) T-CELL AND OTHER IMMUNOTHERAPIES 020 INTRACRANIAL VASCULAR PROCEDURES WITH PRINCIPAL DIAGNOSIS HEMORRHAGE WITH MCC 021 INTRACRANIAL VASCULAR PROCEDURES WITH PRINCIPAL DIAGNOSIS HEMORRHAGE WITH CC 023 CRANIOTOMY WITH MAJOR DEVICE IMPLANT OR ACUTE COMPLEX CNS PRINCIPAL DIAGNOSIS WITH MCC O 024 CRANIOTOMY WITH MAJOR DEVICE IMPLANT OR ACUTE COMPLEX CNS PRINCIPAL DIAGNOSIS WITHOUT MC 025 CRANIOTOMY AND ENDOVASCULAR INTRACRANIAL PROCEDURES WITH MCC 026 CRANIOTOMY AND ENDOVASCULAR INTRACRANIAL PROCEDURES WITH CC 027 CRANIOTOMY AND ENDOVASCULAR INTRACRANIAL PROCEDURES WITHOUT CC/MCC 028 SPINAL PROCEDURES WITH MCC 029 SPINAL PROCEDURES WITH CC OR SPINAL NEUROSTIMULATORS 030 SPINAL PROCEDURES WITHOUT CC/MCC 031 VENTRICULAR SHUNT PROCEDURES WITH MCC 032 VENTRICULAR SHUNT PROCEDURES WITH CC 033 VENTRICULAR SHUNT PROCEDURES WITHOUT CC/MCC 034 CAROTID ARTERY STENT PROCEDURES WITH MCC 035 CAROTID ARTERY STENT PROCEDURES WITH CC 036 CAROTID ARTERY STENT PROCEDURES WITHOUT CC/MCC 037 EXTRACRANIAL PROCEDURES WITH MCC 038 EXTRACRANIAL PROCEDURES WITH CC 039 EXTRACRANIAL PROCEDURES WITHOUT CC/MCC 040 PERIPHERAL, CRANIAL NERVE AND OTHER NERVOUS SYSTEM PROCEDURES WITH MCC 041 PERIPHERAL, CRANIAL NERVE AND OTHER NERVOUS SYSTEM PROCEDURES WITH CC OR PERIPHERAL NEUR 042 PERIPHERAL, CRANIAL NERVE AND OTHER NERVOUS SYSTEM PROCEDURES WITHOUT CC/MCC 052 SPINAL DISORDERS AND INJURIES WITH CC/MCC 054 NERVOUS SYSTEM NEOPLASMS WITH MCC 055 NERVOUS SYSTEM NEOPLASMS WITHOUT MCC 056 DEGENERATIVE NERVOUS SYSTEM DISORDERS WITH MCC 057 DEGENERATIVE NERVOUS SYSTEM DISORDERS WITHOUT MCC 058 MULTIPLE SCLEROSIS AND CEREBELLAR ATAXIA WITH MCC 059 MULTIPLE SCLEROSIS AND CEREBELLAR ATAXIA WITH CC 060 MULTIPLE SCLEROSIS AND CEREBELLAR ATAXIA WITHOUT CC/MCC 061 ISCHEMIC STROKE, PRECEREBRAL OCCLUSION OR TRANSIENT ISCHEMIA WITH THROMBOLYTIC AGENT WIT 062 ISCHEMIC STROKE, PRECEREBRAL OCCLUSION OR TRANSIENT ISCHEMIA WITH THROMBOLYTIC AGENT WIT 063 ISCHEMIC STROKE, PRECEREBRAL OCCLUSION OR TRANSIENT ISCHEMIA WITH THROMBOLYTIC AGENT WIT 064 INTRACRANIAL HEMORRHAGE OR CEREBRAL INFARCTION WITH MCC 065 INTRACRANIAL HEMORRHAGE OR CEREBRAL INFARCTION WITH CC OR TPA IN 24 HOURS 066 INTRACRANIAL HEMORRHAGE OR CEREBRAL INFARCTION WITHOUT CC/MCC 067 NONSPECIFIC CVA AND PRECEREBRAL OCCLUSION WITHOUT INFARCTION WITH MCC 068 NONSPECIFIC CVA AND PRECEREBRAL OCCLUSION WITHOUT INFARCTION WITHOUT MCC 069 TRANSIENT ISCHEMIA WITHOUT THROMBOLYTIC 070 NONSPECIFIC CEREBROVASCULAR DISORDERS WITH MCC 071 NONSPECIFIC CEREBROVASCULAR DISORDERS WITH CC 072 NONSPECIFIC CEREBROVASCULAR DISORDERS WITHOUT CC/MCC 073 CRANIAL AND PERIPHERAL NERVE DISORDERS WITH MCC 074 CRANIAL AND PERIPHERAL NERVE DISORDERS WITHOUT MCC 077 HYPERTENSIVE ENCEPHALOPATHY WITH MCC 078 HYPERTENSIVE ENCEPHALOPATHY WITH CC 080 NONTRAUMATIC STUPOR AND COMA WITH MCC 081 NONTRAUMATIC STUPOR AND COMA WITHOUT MCC 082 TRAUMATIC STUPOR AND COMA >1 HOUR WITH MCC 083 TRAUMATIC STUPOR AND COMA >1 HOUR WITH CC 084 TRAUMATIC STUPOR AND COMA >1 HOUR WITHOUT CC/MCC 085 TRAUMATIC STUPOR AND COMA <1 HOUR WITH MCC 086 TRAUMATIC STUPOR AND COMA <1 HOUR WITH CC 087 TRAU

In [0]:
from pyspark.sql.types import *
import json

jschemadrg = '{"fields":[{"metadata":{},"name":"DRG_Cd","nullable":true,"type":"string"},{"metadata":{},"name":"DRG_Desc","nullable":true,"type":"string"}],"type":"struct"}'

schemadrg = StructType.fromJson(json.loads(jschemadrg))

In [0]:
dfdrg.write.mode("overwrite").format("delta").option("mergeSchema", "true").option("schema", "schemadrg").save("/mnt/sink/" + sinkAdlsFolderName + user + "/gold/drg")

In [0]:
from  pyspark.sql.functions import *    
sqlstringfact = "select twodigityear, DRG_Cd, Rndrng_Prvdr_CCN, Rndrng_Prvdr_Org_Name, Rndrng_Prvdr_City, Rndrng_Prvdr_St, Rndrng_Prvdr_State_FIPS, Rndrng_Prvdr_Zip5, Rndrng_Prvdr_State_Abrvtn, Rndrng_Prvdr_RUCA, Rndrng_Prvdr_RUCA_Desc, Tot_Dschrgs, Avg_Submtd_Cvrd_Chrg, Avg_Tot_Pymt_Amt, Avg_Mdcr_Pymt_Amt from " + usertable + " order by twodigityear, DRG_Cd, Rndrng_Prvdr_CCN"
dffact = spark.sql(sqlstringfact)
display(dffact)

twodigityear DRG_Cd Rndrng_Prvdr_CCN Rndrng_Prvdr_Org_Name Rndrng_Prvdr_City Rndrng_Prvdr_St Rndrng_Prvdr_State_FIPS Rndrng_Prvdr_Zip5 Rndrng_Prvdr_State_Abrvtn Rndrng_Prvdr_RUCA Rndrng_Prvdr_RUCA_Desc Tot_Dschrgs Avg_Submtd_Cvrd_Chrg Avg_Tot_Pymt_Amt Avg_Mdcr_Pymt_Amt 13 001 30103 Mayo Clinic Hospital Phoenix 5777 East Mayo Boulevard 04 85054 AZ 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 17 493283.34 217694.06 180084.94 13 001 40114 Baptist Health Medical Center-Little Rock Little Rock 9601 Interstate 630, Exit 7 05 72205 AR 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 14 817895.5 212748.14 180063.14 13 001 50100 Sharp Memorial Hospital San Diego 7901 Frost St 06 92123 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 15 1062699.1 272182.0 187225.73 13 001 50108 Sutter General Hospital Sacramento 2801 L Street 06 95816 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 17 862402.1 253741.17 249268.47 13 001 50262 Ronald Reagan Ucla Medical Center Los Angeles 757 Westwood Plaza 06 90095 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 12 1221108.9 366463.25 330515.6 13 001 50454 Ucsf Medical Center San Francisco 505 Parnassus Ave, Box 0296 06 94143 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 15 1786987.9 424731.12 401234.06 13 001 50625 Cedars-Sinai Medical Center Los Angeles 8700 Beverly Blvd 06 90048 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 31 1980414.0 318322.75 305622.1 13 001 50696 Keck Hospital Of Usc Los Angeles 1500 San Pablo St 06 90033 CA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 12 1374975.1 279407.6 255963.75 13 001 70025 Hartford Hospital Hartford 80 Seymour Street 09 06102 CT 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 11 542489.75 239404.73 196416.1 13 001 90011 Medstar Washington Hospital Center Washington 110 Irving St Nw 11 20010 DC 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 23 799811.56 264948.7 203967.48 13 001 100113 Uf Health Shands Hospital Gainesville 1600 Sw Archer Rd 12 32610 FL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 16 633454.56 239405.25 227043.69 13 001 100128 Tampa General Hospital Tampa 1 Tampa General Circle 12 33606 FL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 27 956004.75 203774.27 194855.52 13 001 100151 Mayo Clinic Jacksonville 4500 San Pablo Rd 12 32224 FL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 15 473145.34 204253.6 143860.6 13 001 110010 Emory University Hospital Atlanta 1364 Clifton Road, Ne 13 30322 GA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 20 491566.16 219322.45 179458.3 13 001 110083 Piedmont Hospital Atlanta 1968 Peachtree Rd Nw 13 30309 GA 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 19 984263.4 236742.2 230621.95 13 001 140088 The University Of Chicago Medical Center Chicago 5841 South Maryland 17 60637 IL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 38 1252026.4 294675.72 281653.6 13 001 140208 Advocate Christ Hospital & Medical Center Oak Lawn 4440 W 95th Street 17 60453 IL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 42 796901.8 287975.1 206701.1 13 001 140276 Loyola University Medical Center Maywood 2160 S 1st Avenue 17 60153 IL 1 Metropolitan area core: primary flow within an urbanized area of 50,000 and greater 16 614812.44 228073.25 215977.25 13 001 140281 Northwestern Memorial Hospital Chicago 251 E Huron St 17 60611 IL 1 Metropolitan area core: primary flow

In [0]:
from pyspark.sql.types import *
import json

jschemafact = '{"fields":[{"metadata":{},"name":"twodigityear","nullable":true,"type":"string"},{"metadata":{},"name":"DRG_Cd","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_CCN","nullable":true,"type":"integer"},{"metadata":{},"name":"Rndrng_Prvdr_Org_Name","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_City","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_St","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_State_FIPS","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_Zip5","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_State_Abrvtn","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_RUCA","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_RUCA_Desc","nullable":true,"type":"string"},{"metadata":{},"name":"Tot_Dschrgs","nullable":true,"type":"integer"},{"metadata":{},"name":"Avg_Submtd_Cvrd_Chrg","nullable":true,"type":"float"},{"metadata":{},"name":"Avg_Tot_Pymt_Amt","nullable":true,"type":"float"},{"metadata":{},"name":"Avg_Mdcr_Pymt_Amt","nullable":true,"type":"float"}],"type":"struct"}'

schemafact = StructType.fromJson(json.loads(jschemafact))

In [0]:
dffact.write.mode("overwrite").format("delta").option("mergeSchema", "true").option("schema", "schemafact").save("/mnt/sink/" + sinkAdlsFolderName + user + "/gold/medicareinpatientfact")

In [0]:
spark.sql("CREATE DATABASE IF NOT EXISTS " + catalogdatabaseschema + "")
spark.sql("CREATE TABLE IF NOT EXISTS " + catalogdatabaseschema + ".datedim" + user + " USING DELTA LOCATION \
'" + abfsspath + "/date/'")

DataFrame[]

In [0]:
spark.sql("CREATE DATABASE IF NOT EXISTS " + catalogdatabaseschema + "")
spark.sql("CREATE TABLE IF NOT EXISTS " + catalogdatabaseschema + ".drgdim" + user + " USING DELTA LOCATION \
'" + abfsspath + "/drg/'")

DataFrame[]

In [0]:
spark.sql("CREATE DATABASE IF NOT EXISTS " + catalogdatabaseschema + "")
spark.sql("CREATE TABLE IF NOT EXISTS " + catalogdatabaseschema + ".medicareinpatientfact" + user + " USING DELTA LOCATION \
'" + abfsspath + "/medicareinpatientfact/'")

DataFrame[]

#This is a fix for a S3 delta table below

In [0]:
import pandas as pd

url = 'https://raw.githubusercontent.com/DataSnowman/adbfundamentalsws/main/data/diabetes/DiabetesProviders.csv'
dfdia = pd.read_csv(url)
dfdia.head(15)

Rndrng_Prvdr_CCN                  Rndrng_Prvdr_Org_Name  Max
0              10001        Southeast Health Medical Center   21
1              10005  Marshall Medical Centers South Campus   21
2              10006           North Alabama Medical Center   21
3              10011                      St Vincent's East   21
4              10012         Dekalb Regional Medical Center   16
5              10016          Shelby Baptist Medical Center   21
6              10019         Helen Keller Memorial Hospital   20
7              10023           Baptist Medical Center South   21
8              10024          Jackson Hospital & Clinic Inc   21
9              10025     George H. Lanier Memorial Hospital   13
10             10029            East Alabama Medical Center   21
11             10033         University Of Alabama Hospital   21
12             10035        Cullman Regional Medical Center   20
13             10036                       Andalusia Health   18
14             10038         Stringfellow Memorial Hospital   20

In [0]:
spark.conf.set("spark.sql.execution.arrow.enabled", "true")

sparkDF=spark.createDataFrame(dfdia)
sparkDF.printSchema()
sparkDF.show()

root
 |-- Rndrng_Prvdr_CCN: long (nullable = true)
 |-- Rndrng_Prvdr_Org_Name: string (nullable = true)
 |-- Max: long (nullable = true)

+----------------+---------------------+---+
|Rndrng_Prvdr_CCN|Rndrng_Prvdr_Org_Name|Max|
+----------------+---------------------+---+
|           10001| Southeast Health ...| 21|
|           10005| Marshall Medical ...| 21|
|           10006| North Alabama Med...| 21|
|           10011|    St Vincent's East| 21|
|           10012| Dekalb Regional M...| 16|
|           10016| Shelby Baptist Me...| 21|
|           10019| Helen Keller Memo...| 20|
|           10023| Baptist Medical C...| 21|
|           10024| Jackson Hospital ...| 21|
|           10025| George H. Lanier ...| 13|
|           10029| East Alabama Medi...| 21|
|           10033| University Of Ala...| 21|
|           10035| Cullman Regional ...| 20|
|           10036|     Andalusia Health| 18|
|           10038| Stringfellow Memo...| 20|
|           10039|  Huntsville Hospital| 21|
|      

In [0]:
from pyspark.sql.types import *
import json

jschemaprov = '{"fields":[{"metadata":{},"name":"Rndrng_Prvdr_CCN","nullable":true,"type":"string"},{"metadata":{},"name":"Rndrng_Prvdr_Org_Name","nullable":true,"type":"string"},{"metadata":{},"name":"twodigityear","nullable":true,"type":"string"}],"type":"struct"}'

schemadrg = StructType.fromJson(json.loads(jschemaprov))

In [0]:
sparkDF.write.mode("overwrite").format("delta").option("mergeSchema", "true").option("schema", "schemaprov").save("/mnt/sink/" + sinkAdlsFolderName + user + "/gold/diabetesproviders")

In [0]:
dfdrg.write.mode("overwrite").format("delta").option("mergeSchema", "true").option("schema", "schemadrg").save("/mnt/sink/" + sinkAdlsFolderName + user + "/gold/drg")